In [1]:
!tensorboard --logdir="../tensorboard/exp/retrain_1000_1000_52"

TensorFlow installation not found - running with reduced feature set.



NOTE: Using experimental fast data loading logic. To disable, pass
    "--load_fast=false" and report issues on GitHub. More details:
    https://github.com/tensorflow/tensorboard/issues/4784

Serving TensorBoard on localhost; to expose to the network, use a proxy or pass --bind_all
TensorBoard 2.15.1 at http://localhost:6007/ (Press CTRL+C to quit)
^C


##### 追加corpus Hi-Fi-Captain Corpus音声を結合して、再生

In [13]:
from IPython.display import Audio
from scipy.io import wavfile
from pydub import AudioSegment
import os

def combine_wav_files(output_file, *input_files):
    combined = AudioSegment.from_wav(input_files[0])

    for input_file in input_files[1:]:
        segment = AudioSegment.from_wav(input_file)
        combined += segment

    combined.export(output_file, format="wav")

In [24]:
out_file = "./hfc-merged-1.wav"
in_dir = "../downloads/hfc_men/all/"
n_skip = 0
n_merging = 10
in_files_all = [file for file in os.listdir(in_dir) if file.endswith(".wav")]

# nこのファイルを選択してpathを取得
selected_files = in_files_all[n_skip:n_merging]
file_paths = [os.path.join(in_dir, file) for file in selected_files]
# 結合
combine_wav_files(out_file, *file_paths)

print("combined files are :")
print(*file_paths, sep="\n")

# 音声の再生
sample_rate, audio_data = wavfile.read("./hfc-merged-1.wav")
Audio(data=audio_data, rate=sample_rate)

combined files are :
../downloads/hfc_men/all/Seikatsu14_B-k2u2_000120.wav
../downloads/hfc_men/all/Seikatsu02_S-A__000120.wav
../downloads/hfc_men/all/Seikatsu04_A-U__000010.wav
../downloads/hfc_men/all/Seikatsu08_B-NA_000070.wav
../downloads/hfc_men/all/Seikatsu04_A-MU_000030.wav
../downloads/hfc_men/all/Seikatsu08_i2-KA_000020.wav
../downloads/hfc_men/all/Seikatsu01_N-TI_000040.wav
../downloads/hfc_men/all/Seikatsu04_A-E__000070.wav
../downloads/hfc_men/all/Seikatsu13_B-KA_000040.wav
../downloads/hfc_men/all/Seikatsu01_B-I__000080.wav


### 追加学習前のJVScorpus-Tacotron2音声比較

#### Tacotron + Parallel WaveGAN (24kHz）

In [3]:
from ttslearn.pretrained import create_tts_engine
import IPython
from IPython.display import Audio
import librosa
import librosa.display
from tqdm.notebook import tqdm
import torch
import random


In [43]:
pwg_engine = create_tts_engine("multspk_tacotron2_pwg_jvs24k", device="mps")
for spk in ["jvs052", "jvs070", "jvs075"]:
    text = "バスルームはお客様のお忘れ物が多いので、まずチェックします。"
    wav, sr = pwg_engine.tts(text, spk_id=pwg_engine.spk2id[spk])
    print(f"Speaker: {spk}")
    print(text)
    IPython.display.display(Audio(wav, rate=sr))

Speaker: jvs052
バスルームはお客様のお忘れ物が多いので、まずチェックします。


Speaker: jvs070
バスルームはお客様のお忘れ物が多いので、まずチェックします。


Speaker: jvs075
バスルームはお客様のお忘れ物が多いので、まずチェックします。


#### Tacotron + HiFi-GAN (24kHz）

In [35]:
# pwg_engine = create_tts_engine("multspk_tacotron2_hifipwg_jvs24k", device="mps")
# for spk in ["jvs021", "jvs022", "jvs023", "jvs024", "jvs025", "jvs026", "jvs027", "jvs028", "jvs029", "jvs030"]:
#     text = "10月なので、まだ長袖がなくても大丈夫かもしれません。"
#     wav, sr = pwg_engine.tts(text, spk_id=pwg_engine.spk2id[spk])
#     print(f"Speaker: {spk}")
#     print(text)
#     IPython.display.display(Audio(wav, rate=sr))

##### HF-CAPTAINに類似する音声idメモ
- jvs052 + + + +
- jvs070 +
- jvs075 + 

比較した結果、声質が最も近いのはid-052と判断。まず、追加学習に052を使用することにする